### Step 2: *Exploratory Data Analysis*

In this notebook, we'll explore the data we've processed in the previous notebook. We'll look at the distribution of the data to try and find trends/patterns. We'll also look for features that could potentially be used to backfill missing data (rideable_type).
 
 Questions to answer:
 - How many rides are there per day?
 - How many stations are added each month/year?
 - How are the stations distributed across the city?
 - What is the average longevity of a citi bike?
 - What is the average trip duration?
 - What is the average trip distance?
 
 We'll answer these questions by creating visualizations of the data.

In [2]:
import polars as pl
import pandas as pd
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go

px.set_mapbox_access_token(open('./tokens/.mapbox_token').read())

In [3]:
'''
Read 2013-2021 data into a lazy frame. Lazy frames are not loaded into memory and will make dealing with large datasets more manageable.
For each visualization, we will load the necessary data into a pandas dataframe through the to_pandas() method.
'''

path = '2013-2021/{}.parquet'

for year in range(2013, 2022):
    if year == 2013:
        df = pl.scan_parquet(path.format(year))
    else:
        df = pl.concat([df, pl.scan_parquet(path.format(year))], how='vertical')

# create columns for filtering
df = df.with_columns([
    pl.col('started_at').dt.year().alias('year'),
    (pl.col('ended_at') - pl.col('started_at')).dt.seconds().alias('duration'),
    pl.col('started_at').dt.date().alias('date'),
    pl.col('started_at').dt.strftime('%Y %m').alias('year_month'),
    pl.col('started_at').dt.hour().alias('hour'),
    pl.col('started_at').dt.strftime('%H:%M').alias('hour_minute')
])

In [8]:
'''
We'll start by visualizing the number of trips per day. We'll use the started_at column to get the date of each trip.
'''
# get counts of trips per day
trips_df = df.group_by('date') \
            .agg(pl.count('date').alias('trip_count')) \
            .sort('date') \
            .collect() \
            .to_pandas()

def show_trips_day(startdate, enddate):
    starttime = pd.to_datetime(startdate)
    endtime = pd.to_datetime(enddate)
    trips = trips_df.loc[trips_df['date'].between(starttime, endtime)]
    fig = px.scatter(trips, x=trips['date'], y=trips['trip_count'], hover_data=['date', 'trip_count'])
    fig.update_layout(
        title='Number of trips per day from {} to {}'.format(startdate, enddate),
        hovermode='x',
        xaxis_title='Date',
        yaxis_title='Number of trips',
        xaxis_tickformat='%B %Y',
        yaxis_range=[0, 120000],
        xaxis_range=[starttime, endtime],)
    fig.show()

# call function. first argument is start date, second argument is end date
show_trips_day('2013-06', '2021-01')

/Users/gunn/repo/citibike_analysis/.venv-cb/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [65]:
# get start_station_name and started_at column as pandas dataframe
stations_df = df.group_by('year_month') \
    .agg(pl.n_unique('start_station_name').alias('no_stations')) \
    .sort('year_month') \
    .collect() \
    .to_pandas()

def show_stations_month(startdate, enddate):
    starttime = pd.to_datetime(startdate)
    endtime = pd.to_datetime(enddate)
    stations_df['date'] = pd.to_datetime(stations_df['year_month'])
    stations_df_filtered = stations_df.loc[stations_df['date'].between(starttime, endtime)]
    fig = px.bar(stations_df_filtered, x='date', y='no_stations')
    fig.update_layout(
        title='Number of stations from {} to {}'.format(startdate, enddate),
        xaxis_title='Date',
        yaxis_title='Number of stations',
        xaxis_tickformat='%B %Y',
        yaxis_range=[0, 1300],
        xaxis_range=[starttime, endtime],)
    fig.show()

show_stations_month('2013-06', '2021-01')

/var/folders/gs/j78wwm4x6p91yqkd3fvdrk240000gn/T/ipykernel_5419/3856466101.py:11: UserWarning:

Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.

/Users/gunn/repo/citibike_analysis/.venv-cb/lib/python3.10/site-packages/_plotly_utils/basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [67]:
# get counts of station_name per year with lat and lng
stations_map_df = df.group_by('year', 'start_station_name') \
    .agg(pl.first('start_lat').alias('start_lat'), pl.first('start_lng').alias('start_lng'), pl.count('start_station_name').alias('counts')) \
    .sort('year') \
    .collect() \
    .to_pandas()

def show_stations_map(startyear, endyear):
    startyear = int(startyear)
    endyear = int(endyear)
    stations_map_df_filtered = stations_map_df.loc[stations_map_df['year'].between(startyear, endyear)]
    fig = px.scatter_mapbox(stations_map_df_filtered, 
                            lat='start_lat', 
                            lon='start_lng', 
                            hover_name='start_station_name', 
                            animation_frame='year', 
                            zoom=10,
                            size='counts',
                            center=dict(lat=40.73944, lon=-73.97681),
                            height=800,
                            )
    fig.update_layout(
        title='Number of stations from {} to {}'.format(startyear, endyear),
        mapbox_style='carto-positron',
        )
    fig.show()

show_stations_map(2013, 2020)

In [68]:
# get bike_id counts by year
bike_df = df.group_by('year', 'bike_id') \
    .agg(pl.count('bike_id').alias('trips_per_bike')) \
    .sort('year') \
    .collect() \
    .to_pandas()

def show_bikes_year(startyear, endyear):
    startyear = int(startyear)
    endyear = int(endyear)
    bike_df_filtered = bike_df.loc[bike_df['year'].between(startyear, endyear)]
    fig = px.scatter(bike_df_filtered, x='bike_id', y='trips_per_bike', animation_frame='year')
    fig.update_layout(
        title='Number of trips per bike (by ID) from {} to {}'.format(startyear, endyear),
        xaxis_title='Bike ID',
        yaxis_title='Number of trips',
        yaxis_range=[0, 3500],
        xaxis_range=[14000, 51000],
    )
    fig.show()

show_bikes_year(2013, 2020)

In [ ]:
# trace locations of bike_id: 15263 

def show_bike_trace(bikeid, df):
    bikeid = int(bikeid)
    bike_df = df.filter(pl.col('bike_id') == bikeid).select(
        pl.col('start_lat'),
        pl.col('start_lng'),
        pl.col('started_at'),
    ).collect().to_pandas()

    fig = px.line_mapbox(bike_df, 
                         lat='start_lat', 
                         lon='start_lng', 
                         hover_name='started_at', 
                         zoom=10, 
                         height=800, 
                         center=dict(lat=40.73944, lon=-73.97681),
                         animation_frame='started_at'
                         )
                         
    fig.update_layout(
        title=f'Location of bike ID: {bikeid} over time',
        mapbox_style='carto-positron')
    fig.show()

show_bike_trace(15263, df)


In [86]:
# extract total number of trips and total number of unique stations per year from each parquet file

averages = df.group_by('year') \
    .agg(
        pl.count('year').alias('total_trips'), 
        pl.n_unique('start_station_name').alias('total_stations'),
        pl.median('duration').alias('median_duration')) \
    .sort('year') \
    .collect() \
    .to_pandas()

averages['trips_per_station'] = averages['total_trips'] / averages['total_stations']

def show_averages(startyear, endyear):
    startyear = int(startyear)
    endyear = int(endyear)
    averages_filtered = averages.loc[averages['year'].between(startyear, endyear)]

    # create subplots
    fig = make_subplots(rows=2, cols=2, subplot_titles=('Total trips', 'Total stations', 'Trips per station', 'Median trip duration'))
    fig.add_trace(go.Scatter(x=averages_filtered['year'], y=averages_filtered['total_trips']), row=1, col=1)
    fig.add_trace(go.Scatter(x=averages_filtered['year'], y=averages_filtered['total_stations']), row=1, col=2)
    fig.add_trace(go.Scatter(x=averages_filtered['year'], y=averages_filtered['trips_per_station']), row=2, col=1)
    fig.add_trace(go.Scatter(x=averages_filtered['year'], y=averages_filtered['median_duration']), row=2, col=2)
    fig.update_layout(
        title='Total trips, stations, trips/station, and median duration',
        xaxis_title='Year',
        yaxis_title='Number of trips',
        xaxis_tickformat='%Y',
        yaxis_range=[0, 25000000],
        xaxis_range=[2013, 2021],
        height=800,
        width=1200,
        )
    fig.show()

show_averages(2013,2020)

In [14]:
byhour = df.group_by('hour_minute') \
    .agg(
        pl.count('started_at').alias('trip_count'),
        pl.median('duration').alias('median_duration'),
    ) \
    .sort('hour_minute') \
    .collect() \
    .to_pandas()  

def show_byhour():
    fig = make_subplots(rows=2, cols=1, subplot_titles=('Number of trips by hour', 'Median trip duration by hour'))
    fig.add_trace(go.Scatter(x=byhour['hour_minute'], y=byhour['trip_count'], line_shape='spline'), row=1, col=1)
    fig.add_hline(y=byhour['trip_count'].mean(), row=1, col=1, line_dash='dash')
    fig.add_trace(go.Scatter(x=byhour['hour_minute'], y=byhour['median_duration'], line_shape='spline'), row=2, col=1)
    fig.add_hline(y=byhour['median_duration'].mean(), row=2, col=1, line_dash='dash')
    fig.update_layout(
        title='Number of trips and median trip duration by hour (2013-2021)',
        xaxis_title='Hour',
        yaxis_title='Number of trips',
        xaxis_tickformat='%H',
        yaxis_range=[0, 200000],
        height=800,
        width=1200,
        )
    fig.show()

show_byhour()

In [36]:
# count member and casual trips per month
# member to member_counts, casual to casual_counts

member_df = df.group_by('year_month', maintain_order=True).agg(
    pl.col('member_casual').value_counts().alias('member_count_struct')
).collect()

# extract member and casual counts from member_df
member_df = member_df.with_columns([
    pl.col('member_count_struct').map_elements(lambda x: x[0]['counts'] if x[0]['member_casual'] == 'member' else x[1]['counts']).alias('member_counts'),
    pl.col('member_count_struct').map_elements(lambda x: x[1]['counts'] if x[1]['member_casual'] == 'casual' else x[0]['counts']).alias('casual_counts'),
]).to_pandas()

member_df['total_counts'] = member_df['member_counts'] + member_df['casual_counts']

In [37]:
# plot bar graph of member and casual counts per month
def show_member_casual(startdate, enddate):
    starttime = startdate
    endtime = enddate
    member_df_filtered = member_df.loc[member_df['year_month'].between(starttime, endtime)]
    fig = px.bar(member_df_filtered, x='year_month', y=['member_counts', 'casual_counts'])
    fig.update_layout(
        title='Member and non-member trips from {} to {}'.format(startdate, enddate),
        xaxis_title='Month',
        yaxis_title='Number of trips',
        xaxis_tickformat='%B %Y',
        yaxis_range=[0, 3000000],
        xaxis_range=[starttime, endtime],)
    fig.show()

show_member_casual('2013-06', '2021-01')

In [38]:
member_df['member_percent'] = member_df['member_counts'] / member_df['total_counts']
member_df['casual_percent'] = member_df['casual_counts'] / member_df['total_counts']

def show_member_casual_percent(startdate, enddate):
# line graph of member and casual percentages per month
    starttime = startdate
    endtime = enddate
    member_df_filtered = member_df.loc[member_df['year_month'].between(starttime, endtime)]
    fig = px.line(member_df_filtered, x='year_month', y=['member_percent', 'casual_percent'])
    fig.update_layout(
        title='Member and non-member trips from {} to {}'.format(startdate, enddate),
        xaxis_title='Month',
        yaxis_title='Percent of trips',
        xaxis_tickformat='%B %Y',
        yaxis_range=[0, 1],
        xaxis_range=[starttime, endtime],)
    fig.show()

show_member_casual_percent('2013-06', '2021-01')

### General Insights 

#### Trips per Day
The number of trips increases at a steady rate from 2013 to 2019, with a slight dip happening in 2020. The dip in 2020 coincides with the start of the pandemic.   
The highest number of trips for a single day was 104,xxx in xxxx.   
Generally, the number of trips falls off during the winter months, increases in the summer months, and peaks in September.

#### Stations
The number of stations increases in phases. 
- 330 stations in 2013
- 470 stations in 2016
- 620 stations in 2017
- 760 stations in 2018
- and a gradual increase starting in Q2 2019 to 1200+ stations in 2020

#### Station Map
The initial rollout of stations were concentrated in Manhattan (south of Central Park) with a few stations in Brooklyn. 
- in 2015, stations expanded north (past E 60th street) and east (further into Brooklyn)
- in 2016, stations continued expanding north and south (to Prospect Park in Brooklyn)
- from 2017 onwards, stations continued expanding north in Manhattan and south and east in Brooklyn.

#### Number of Trips by Bike ID
While it's difficult to say by just looking at the data, if we assume that bike ids are retired and not reused, the average longevity of a bike is suprisingly long. Bike ids from 2013 are still being used in 2020.   
Some interesting points:
- bike id 22000 - 24000 were introduced in 2015 and saw above average use but seem to have been retired (the bikes or the ids) in 2017.
- certain segments of bike ids see much higher usage than others. This could be due to the type of bike (ebikes introduced in 2018), the condition of the bike, or the location of the bike.

#### Averages
The trips per year correlated with the number of stations added each year. 
- This makes sense as more stations means more access and an increase in the number of bikes.
The average number of trips stabilized in 2017 to around 20,000 trips/station/year. The median trip duration stabilized to around 10 minutes in 2017.
- the trips per station drop off in 2020, but the median trip duration increases. This could be due to the pandemic: less people commuting to work, preferring bikes to public transit, and/or using bikes for leisure.

#### By Hour
The number of trips per hour is bimodal, with peaks at 8:45am and 5-6pm. This makes sense as people are commuting to and from work.   
The average trip duration drops around 5am then steadily increases until 3pm, from which point it steadily decreases.

#### Memberships
Overall, both membership rides and casual rides have increased over time. Casual rides have increased at a slightly faster rate than membership rides. Although the most likely cause would be people unsubscribing because they no longer need to commute, the exact reason is unclear with the given data. Since the most recent data point in this data set coincides with the pandemic, the increase in casual rides and drop in membership rides could be a result of a variety of factors.